# IBM Capstone Project: The Battle of Neighbourhoods

# <center>Open a Chinese Restaurant in Toronto, Canada

# Table of Content

[Introduction](#anchors-in-markdown)

[Data](#anchors-in-markdown)

[Methodology](#anchors-in-markdown)

[Result](#anchors-in-markdown)

[Discussion](#anchors-in-markdown)

[Conclusion](#anchors-in-markdown)

# Introduction

Toronto is one of the most diverse cities in the world. The local residents come from more than 100 nationalities and speak more than 140 different languages. Toronto has the largest Chinese ethnic group outside of Asia, and the Chinese restaurant here gathers Sichuan, Hunan, Cantonese and even northern dishes. These Chinese restaurants are located in Chinatown in the city center, as well as Scarborough, Richmond Hill, Markham and Mississauga in the north. Chinese cuisine attracts many tourists and local residents in Toronto.

The objective of this project is to find the most suitable location for the client to open a Chinese restaurant in Toronto. I will use machine learning skills such as K-means to analyse data extracted from various sources to find the best solution for my client. My target audience is entrepreneur who wants to open a Chinese restaurant in Toronto, and need suggestions on the best location to operate the restaurants.

# Data

*   Neighborhoods data: Scarpping list of neighborhoods in Toronto from Wikipedia. <br/> 
[Neighbourhood data link](https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M)

*   Latitude and Longitude data: Getting the geographical coordinates data of each postal code from a csv file. <br/>
[Geographical coordinates data](https://cocl.us/Geospatial_data)


* Venue data: Getting venue data from Foursquare API.

## Scraping data from Wikipedia

In [2]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Solving environment: done


==> WARNING: A newer version of conda exists. <==
  current version: 4.8.2
  latest version: 4.8.3

Please update conda by running

    $ conda update -n base -c defaults conda



## Package Plan ##

  environment location: /opt/anaconda3

  added / updated specs:
    - geopy


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    conda-4.8.3                |   py37hc8dfbb8_1         3.0 MB  conda-forge
    geographiclib-1.50         |             py_0          34 KB  conda-forge
    geopy-2.0.0                |     pyh9f0ad1d_0          63 KB  conda-forge
    python_abi-3.7             |          1_cp37m           4 KB  conda-forge
    ------------------------------------------------------------
                                           Total:         3.1 MB

The following NEW packages will be INSTALLED:

  geographiclib      conda-forge/noarch::geographiclib-1.50

In [3]:
from bs4 import BeautifulSoup
import requests

In [4]:
wiki_url = "https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M"
response = requests.get(wiki_url)
soup = BeautifulSoup(response.text, 'html.parser')

In [5]:
table = soup.find('table').tbody
rows = table.find_all('tr')
columns = [v.text.replace('\n', '') for v in rows[0].find_all('th')]

In [6]:
df = pd.DataFrame(columns = columns)
for i in range(1, len(rows)):
    tds = rows[i].find_all('td')
    
    if len(tds) == 3:
        values = [tds[0].text.replace('\n',''), tds[1].text.replace('\n', ''), tds[2].text.replace('\n', '')]
    else: 
        values = [td.text for td in tds]
    df = df.append(pd.Series(values, index = columns), ignore_index = True)

In [7]:
df.head()

Postal Code           Borough               Neighborhood
0         M1A      Not assigned               Not assigned
1         M2A      Not assigned               Not assigned
2         M3A        North York                  Parkwoods
3         M4A        North York           Victoria Village
4         M5A  Downtown Toronto  Regent Park, Harbourfront

In [8]:
df.columns = ['PostalCode', 'Borough', 'Neighborhood']
df.head()

PostalCode           Borough               Neighborhood
0        M1A      Not assigned               Not assigned
1        M2A      Not assigned               Not assigned
2        M3A        North York                  Parkwoods
3        M4A        North York           Victoria Village
4        M5A  Downtown Toronto  Regent Park, Harbourfront

In [9]:
# Ignore cells with a borough that is 'Not assigned'.
df=df[df['Borough']!='Not assigned']
# Reset index
df=df.reset_index(drop=True)
df.head()

PostalCode           Borough                                 Neighborhood
0        M3A        North York                                    Parkwoods
1        M4A        North York                             Victoria Village
2        M5A  Downtown Toronto                    Regent Park, Harbourfront
3        M6A        North York             Lawrence Manor, Lawrence Heights
4        M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government

In [10]:
df.shape

(103, 3)

## Merge df with latitude and the longitude coordinates of each neighborhood.

In [11]:
# read csv
coord=pd.read_csv("https://cocl.us/Geospatial_data")
coord.head()

Postal Code   Latitude  Longitude
0         M1B  43.806686 -79.194353
1         M1C  43.784535 -79.160497
2         M1E  43.763573 -79.188711
3         M1G  43.770992 -79.216917
4         M1H  43.773136 -79.239476

In [12]:
coord.rename(columns={'Postal Code':'PostalCode'},inplace=True)
coord.head()

PostalCode   Latitude  Longitude
0        M1B  43.806686 -79.194353
1        M1C  43.784535 -79.160497
2        M1E  43.763573 -79.188711
3        M1G  43.770992 -79.216917
4        M1H  43.773136 -79.239476

In [13]:
df1 = pd.merge(df, coord, on='PostalCode')
df1.head()

PostalCode           Borough                                 Neighborhood  \
0        M3A        North York                                    Parkwoods   
1        M4A        North York                             Victoria Village   
2        M5A  Downtown Toronto                    Regent Park, Harbourfront   
3        M6A        North York             Lawrence Manor, Lawrence Heights   
4        M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government   

    Latitude  Longitude  
0  43.753259 -79.329656  
1  43.725882 -79.315572  
2  43.654260 -79.360636  
3  43.718518 -79.464763  
4  43.662301 -79.389494

## Explore the neighborhoods in Toronto

Use geopy library to get the latitude and longitude values of Toronto

In [14]:
address = 'Toronto, ON'

geolocator = Nominatim(user_agent="trt_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Toronto are 43.6534817, -79.3839347.


Create a map of Toronto with neighborhoods superimposed on top.

In [15]:
# Create map of Toronto using latitude and longitude values
map_trt = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(df1['Latitude'], df1['Longitude'], df1['Borough'], df1['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_trt)  
    
map_trt

Define Foursquare Credentials and Version

In [16]:
CLIENT_ID = 'AG3X11IGOLBVP4HPRYAFPA52CPR2QEMB2ICT4SOZNNUA1F1I' # your Foursquare ID
CLIENT_SECRET = '1MK3XD151SDTLT3UHDO53TUCI3H1LI2V1O3UUAFRRKPOZQOT' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: AG3X11IGOLBVP4HPRYAFPA52CPR2QEMB2ICT4SOZNNUA1F1I
CLIENT_SECRET:1MK3XD151SDTLT3UHDO53TUCI3H1LI2V1O3UUAFRRKPOZQOT


Create a function to repeat the same process to all the neighborhoods in Toronto, and create a new dataframe called trt_venues.

In [17]:
LIMIT = 100
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

trt_venues = getNearbyVenues(names=df1['Neighborhood'],
                                   latitudes=df1['Latitude'],
                                   longitudes=df1['Longitude']
                                  )

Parkwoods
Victoria Village
Regent Park, Harbourfront
Lawrence Manor, Lawrence Heights
Queen's Park, Ontario Provincial Government
Islington Avenue, Humber Valley Village
Malvern, Rouge
Don Mills
Parkview Hill, Woodbine Gardens
Garden District, Ryerson
Glencairn
West Deane Park, Princess Gardens, Martin Grove, Islington, Cloverdale
Rouge Hill, Port Union, Highland Creek
Don Mills
Woodbine Heights
St. James Town
Humewood-Cedarvale
Eringate, Bloordale Gardens, Old Burnhamthorpe, Markland Wood
Guildwood, Morningside, West Hill
The Beaches
Berczy Park
Caledonia-Fairbanks
Woburn
Leaside
Central Bay Street
Christie
Cedarbrae
Hillcrest Village
Bathurst Manor, Wilson Heights, Downsview North
Thorncliffe Park
Richmond, Adelaide, King
Dufferin, Dovercourt Village
Scarborough Village
Fairview, Henry Farm, Oriole
Northwood Park, York University
East Toronto, Broadview North (Old East York)
Harbourfront East, Union Station, Toronto Islands
Little Portugal, Trinity
Kennedy Park, Ionview, East Birchmo

In [18]:
trt_venues.shape

(2130, 7)

In [19]:
trt_venues.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0         Parkwoods              43.753259              -79.329656   
1         Parkwoods              43.753259              -79.329656   
2  Victoria Village              43.725882              -79.315572   
3  Victoria Village              43.725882              -79.315572   
4  Victoria Village              43.725882              -79.315572   

                    Venue  Venue Latitude  Venue Longitude  \
0         Brookbanks Park       43.751976       -79.332140   
1           Variety Store       43.751974       -79.333114   
2  Victoria Village Arena       43.723481       -79.315635   
3               Portugril       43.725819       -79.312785   
4             Tim Hortons       43.725517       -79.313103   

          Venue Category  
0                   Park  
1      Food & Drink Shop  
2           Hockey Arena  
3  Portuguese Restaurant  
4            Coffee Shop

Check how many venues were returned for each neighborhood

In [20]:
trt_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                                
Agincourt                                                               5   
Alderwood, Long Branch                                                  9   
Bathurst Manor, Wilson Heights, Downsview North                        22   
Bayview Village                                                         4   
Bedford Park, Lawrence Manor East                                      24   
Berczy Park                                                            59   
Birch Cliff, Cliffside West                                             4   
Brockton, Parkdale Village, Exhibition Place                           23   
Business reply mail Processing Centre, South Ce...                     16   
CN Tower, King and Spadina, Railway Lands, Harb...                     16   
Caledonia-Fairbanks                                                     4   
Canada Post Gateway Processing Centre                                  13   
Cedarbrae                                                               8   
Central Bay Street                                                     68   
Christie                                                               16   
Church and Wellesley                                                   74   
Clarks Corners, Tam O'Shanter, Sullivan                                13   
Cliffside, Cliffcrest, Scarborough Village West                         3   
Commerce Court, Victoria Hotel                                        100   
Davisville                                                             32   
Davisville North                                                       10   
Del Ray, Mount Dennis, Keelsdale and Silverthorn                        4   
Don Mills                                                              27   
Dorset Park, Wexford Heights, Scarborough Town ...                      6   
Downsview                                                              15   
Dufferin, Dovercourt Village                                           17   
East Toronto, Broadview North (Old East York)                           4   
Eringate, Bloordale Gardens, Old Burnhamthorpe,...                      7   
Fairview, Henry Farm, Oriole                                           65   
First Canadian Place, Underground city                                100   
Forest Hill North & West, Forest Hill Road Park                         4   
Garden District, Ryerson                                              100   
Glencairn                                                               5   
Golden Mile, Clairlea, Oakridge                                         8   
Guildwood, Morningside, West Hill                                       8   
Harbourfront East, Union Station, Toronto Islands                     100   
High Park, The Junction South                                          24   
Hillcrest Village                                                       4   
Humber Summit                                                           3   
Humberlea, Emery                                                        1   
Humewood-Cedarvale                                                      4   
India Bazaar, The Beaches West                                         21   
Kennedy Park, Ionview, East Birchmount Park                             5   
Kensington Market, Chinatown, Grange Park                              59   
Kingsview Village, St. Phillips, Martin Grove G...                      4   
Lawrence Manor, Lawrence Heights                                       12   
Lawrence Park                                                           4   
Leaside                                                                34   
Little Portugal, Trinity                                               44   
Malvern, Rouge                                                          1   
Milliken, Agincourt North, Steeles East, L'Amor.

In [21]:
print('There are {} uniques categories.'.format(len(trt_venues['Venue Category'].unique())))

There are 268 uniques categories.


Print out the list of categories

In [22]:
trt_venues['Venue Category'].unique()

array(['Park', 'Food & Drink Shop', 'Hockey Arena',
       'Portuguese Restaurant', 'Coffee Shop', 'Pizza Place',
       'Financial or Legal Service', 'Bakery', 'Distribution Center',
       'Spa', 'Pub', 'Restaurant', 'Breakfast Spot',
       'Gym / Fitness Center', 'Historic Site', 'Farmers Market',
       'Performing Arts Venue', 'Chocolate Shop', 'Dessert Shop',
       'French Restaurant', 'Café', 'Yoga Studio', 'Theater',
       'Event Space', 'Shoe Store', 'Ice Cream Shop', 'Art Gallery',
       'Cosmetics Shop', 'Asian Restaurant', 'Electronics Store', 'Bank',
       'Beer Store', 'Health Food Store', 'Wine Shop', 'Antique Shop',
       'Boutique', 'Furniture / Home Store', 'Vietnamese Restaurant',
       'Clothing Store', 'Accessories Store', 'Miscellaneous Shop',
       'Gift Shop', 'Italian Restaurant', 'Sushi Restaurant', 'Creperie',
       'Beer Bar', 'Arts & Crafts Store', 'Burrito Place',
       'Mexican Restaurant', 'Hobby Shop', 'Diner', 'Fried Chicken Joint',
       'D

Check if the results contain "Chinese Restaurant".

In [23]:
"Chinese Restaurant" in trt_venues['Venue Category'].unique()

True

Analyze each neighborhood

In [24]:
# one hot encoding
trt_onehot = pd.get_dummies(trt_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
trt_onehot['Neighborhood'] = trt_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [trt_onehot.columns[-1]] + list(trt_onehot.columns[:-1])
trt_onehot = trt_onehot[fixed_columns]

trt_onehot.head()

Yoga Studio  Accessories Store  Afghan Restaurant  Airport  \
0            0                  0                  0        0   
1            0                  0                  0        0   
2            0                  0                  0        0   
3            0                  0                  0        0   
4            0                  0                  0        0   

   Airport Food Court  Airport Lounge  Airport Service  Airport Terminal  \
0                   0               0                0                 0   
1                   0               0                0                 0   
2                   0               0                0                 0   
3                   0               0                0                 0   
4                   0               0                0                 0   

   American Restaurant  Antique Shop  Aquarium  Art Gallery  Art Museum  \
0                    0             0         0            0           0   
1                    0             0         0            0           0   
2                    0             0         0            0           0   
3                    0             0         0            0           0   
4                    0             0         0            0           0   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  Auto Garage  \
0                    0                 0                   0            0   
1                    0                 0                   0            0   
2                    0                 0                   0            0   
3                    0                 0                   0            0   
4                    0                 0                   0            0   

   Auto Workshop  BBQ Joint  Baby Store  Bagel Shop  Bakery  Bank  Bar  \
0              0          0           0           0       0     0    0   
1              0          0           0           0       0     0    0   
2              0          0           0           0       0     0    0   
3              0          0           0           0       0     0    0   
4              0          0           0           0       0     0    0   

   Baseball Field  Baseball Stadium  Basketball Court  Basketball Stadium  \
0               0                 0                 0                   0   
1               0                 0                 0                   0   
2               0                 0                 0                   0   
3               0                 0                 0                   0   
4               0                 0                 0                   0   

   Beach  Bed & Breakfast  Beer Bar  Beer Store  Belgian Restaurant  \
0      0                0         0           0                   0   
1      0                0         0           0                   0   
2      0                0         0           0                   0   
3      0                0         0           0                   0   
4      0                0         0           0                   0   

   Bike Shop  Bistro  Boat or Ferry  Bookstore  Boutique  \
0          0       0              0          0         0   
1          0       0              0          0         0   
2          0       0              0          0         0   
3          0       0              0          0         0   
4          0       0              0          0         0   

   Brazilian Restaurant  Breakfast Spot  Brewery  Bridal Shop  \
0                     0               0        0            0   
1                     0               0        0            0   
2                     0               0        0            0   
3                     0               0        0            0   
4                     0               0        0            0   

   Bubble Tea Shop  Building  Burger Joint  Burrito Place  Bus Line  \
0                0         0             0              0         0   
1           

Group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [25]:
trt_grouped = trt_onehot.groupby('Neighborhood').mean().reset_index()
trt_grouped

Neighborhood  Yoga Studio  \
0                                           Agincourt     0.000000   
1                              Alderwood, Long Branch     0.000000   
2     Bathurst Manor, Wilson Heights, Downsview North     0.000000   
3                                     Bayview Village     0.000000   
4                   Bedford Park, Lawrence Manor East     0.000000   
5                                         Berczy Park     0.000000   
6                         Birch Cliff, Cliffside West     0.000000   
7        Brockton, Parkdale Village, Exhibition Place     0.000000   
8   Business reply mail Processing Centre, South C...     0.000000   
9   CN Tower, King and Spadina, Railway Lands, Har...     0.000000   
10                                Caledonia-Fairbanks     0.000000   
11              Canada Post Gateway Processing Centre     0.000000   
12                                          Cedarbrae     0.000000   
13                                 Central Bay Street     0.014706   
14                                           Christie     0.000000   
15                               Church and Wellesley     0.027027   
16            Clarks Corners, Tam O'Shanter, Sullivan     0.000000   
17    Cliffside, Cliffcrest, Scarborough Village West     0.000000   
18                     Commerce Court, Victoria Hotel     0.000000   
19                                         Davisville     0.000000   
20                                   Davisville North     0.000000   
21   Del Ray, Mount Dennis, Keelsdale and Silverthorn     0.000000   
22                                          Don Mills     0.000000   
23  Dorset Park, Wexford Heights, Scarborough Town...     0.000000   
24                                          Downsview     0.000000   
25                       Dufferin, Dovercourt Village     0.000000   
26      East Toronto, Broadview North (Old East York)     0.000000   
27  Eringate, Bloordale Gardens, Old Burnhamthorpe...     0.000000   
28                       Fairview, Henry Farm, Oriole     0.000000   
29             First Canadian Place, Underground city     0.000000   
30    Forest Hill North & West, Forest Hill Road Park     0.000000   
31                           Garden District, Ryerson     0.000000   
32                                          Glencairn     0.000000   
33                    Golden Mile, Clairlea, Oakridge     0.000000   
34                  Guildwood, Morningside, West Hill     0.000000   
35  Harbourfront East, Union Station, Toronto Islands     0.000000   
36                      High Park, The Junction South     0.000000   
37                                  Hillcrest Village     0.000000   
38                                      Humber Summit     0.000000   
39                                   Humberlea, Emery     0.000000   
40                                 Humewood-Cedarvale     0.000000   
41                     India Bazaar, The Beaches West     0.000000   
42        Kennedy Park, Ionview, East Birchmount Park     0.000000   
43          Kensington Market, Chinatown, Grange Park     0.000000   
44  Kingsview Village, St. Phillips, Martin Grove ...     0.000000   
45                   Lawrence Manor, Lawrence Heights     0.000000   
46                                      Lawrence Park     0.000000   
47                                            Leaside     0.000000   
48                           Little Portugal, Trinity     0.022727   
49                                     Malvern, Rouge     0.000000   
50  Milliken, Agincourt North, Steeles East, L'Amo...     0.000000   
51  Mimico NW, The Queensway West, South of Bloor,...     0.000000   
52                        Moore Park, Summerhill East     0.000000   
53       New Toronto, Mimico South, Humber Bay Shores     0.000000   
54           North Park, Maple Leaf Park, Upwood Park     0.000000   
55                 North Toronto West,  Lawrence Park     0.052632   
56                Northwest, West Humber - Clairvil

In [26]:
len(trt_grouped[trt_grouped["Chinese Restaurant"] > 0])

14

In [27]:
trt_chnres = trt_grouped[["Neighborhood","Chinese Restaurant"]]
trt_chnres.head()

Neighborhood  Chinese Restaurant
0                                        Agincourt                0.00
1                           Alderwood, Long Branch                0.00
2  Bathurst Manor, Wilson Heights, Downsview North                0.00
3                                  Bayview Village                0.25
4                Bedford Park, Lawrence Manor East                0.00

## Cluster the neighborhoods in Toronto

Run k-means to cluster the neighborhood into 5 clusters.

In [28]:
# set number of clusters
kclusters = 5

trt_grouped_clustering = trt_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(trt_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([1, 1, 1, 1, 1, 1, 1, 1, 1, 1], dtype=int32)

Create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.

In [29]:
# add clustering labels
trt_merged = trt_chnres.copy()
trt_merged["Cluster Labels"] = kmeans.labels_

In [30]:
trt_merged.rename(columns={"Neighborhood": "Neighborhood"}, inplace=True)
trt_merged.head()

Neighborhood  Chinese Restaurant  \
0                                        Agincourt                0.00   
1                           Alderwood, Long Branch                0.00   
2  Bathurst Manor, Wilson Heights, Downsview North                0.00   
3                                  Bayview Village                0.25   
4                Bedford Park, Lawrence Manor East                0.00   

   Cluster Labels  
0               1  
1               1  
2               1  
3               1  
4               1

In [31]:
# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
trt_merged = trt_merged.join(trt_venues.set_index("Neighborhood"), on="Neighborhood")

trt_merged.head()

Neighborhood  Chinese Restaurant  Cluster Labels  Neighborhood Latitude  \
0    Agincourt                 0.0               1                43.7942   
0    Agincourt                 0.0               1                43.7942   
0    Agincourt                 0.0               1                43.7942   
0    Agincourt                 0.0               1                43.7942   
0    Agincourt                 0.0               1                43.7942   

   Neighborhood Longitude                        Venue  Venue Latitude  \
0              -79.262029  Panagio's Breakfast & Lunch       43.792370   
0              -79.262029                     Twilight       43.791999   
0              -79.262029                El Pulgarcito       43.792648   
0              -79.262029                       Mark's       43.791179   
0              -79.262029              Commander Arena       43.794867   

   Venue Longitude             Venue Category  
0       -79.260203             Breakfast Spot  
0       -79.258584                     Lounge  
0       -79.259208  Latin American Restaurant  
0       -79.259714             Clothing Store  
0       -79.267989               Skating Rink

Visualize the resulting clusters

In [32]:
# create map
trt_merged.dropna(subset=['Cluster Labels'], inplace=True)
trt_merged['Cluster Labels']=trt_merged['Cluster Labels'].astype('int32')

map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(trt_merged['Neighborhood Latitude'], trt_merged['Neighborhood Longitude'], trt_merged['Neighborhood'], trt_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

## Examine Clusters

Cluster 0

In [33]:
trt_merged.loc[trt_merged['Cluster Labels'] == 0]

Neighborhood  Chinese Restaurant  \
50  Milliken, Agincourt North, Steeles East, L'Amo...                 0.0   
50  Milliken, Agincourt North, Steeles East, L'Amo...                 0.0   
65                                           Rosedale                 0.0   
65                                           Rosedale                 0.0   
65                                           Rosedale                 0.0   
65                                           Rosedale                 0.0   
70                                Scarborough Village                 0.0   
70                                Scarborough Village                 0.0   

    Cluster Labels  Neighborhood Latitude  Neighborhood Longitude  \
50               0              43.815252              -79.284577   
50               0              43.815252              -79.284577   
65               0              43.679563              -79.377529   
65               0              43.679563              -79.377529   
65               0              43.679563              -79.377529   
65               0              43.679563              -79.377529   
70               0              43.744734              -79.239476   
70               0              43.744734              -79.239476   

                                Venue  Venue Latitude  Venue Longitude  \
50                    Port Royal Park       43.815477       -79.289773   
50  Milliken Public School Playground       43.815383       -79.289867   
65                      Rosedale Park       43.682328       -79.378934   
65                       Whitney Park       43.682036       -79.373788   
65               Alex Murray Parkette       43.678300       -79.382773   
65                     Milkman's Lane       43.676352       -79.373842   
70                       McCowan Park       43.745089       -79.239336   
70                         Tumbe Cafe       43.744058       -79.244021   

   Venue Category  
50           Park  
50     Playground  
65     Playground  
65           Park  
65           Park  
65          Trail  
70     Playground  
70  Grocery Store

Cluster 1

In [34]:
trt_merged.loc[trt_merged['Cluster Labels'] == 1]

Neighborhood  Chinese Restaurant  \
0                                           Agincourt            0.000000   
0                                           Agincourt            0.000000   
0                                           Agincourt            0.000000   
0                                           Agincourt            0.000000   
0                                           Agincourt            0.000000   
1                              Alderwood, Long Branch            0.000000   
1                              Alderwood, Long Branch            0.000000   
1                              Alderwood, Long Branch            0.000000   
1                              Alderwood, Long Branch            0.000000   
1                              Alderwood, Long Branch            0.000000   
1                              Alderwood, Long Branch            0.000000   
1                              Alderwood, Long Branch            0.000000   
1                              Alderwood, Long Branch            0.000000   
1                              Alderwood, Long Branch            0.000000   
2     Bathurst Manor, Wilson Heights, Downsview North            0.000000   
2     Bathurst Manor, Wilson Heights, Downsview North            0.000000   
2     Bathurst Manor, Wilson Heights, Downsview North            0.000000   
2     Bathurst Manor, Wilson Heights, Downsview North            0.000000   
2     Bathurst Manor, Wilson Heights, Downsview North            0.000000   
2     Bathurst Manor, Wilson Heights, Downsview North            0.000000   
2     Bathurst Manor, Wilson Heights, Downsview North            0.000000   
2     Bathurst Manor, Wilson Heights, Downsview North            0.000000   
2     Bathurst Manor, Wilson Heights, Downsview North            0.000000   
2     Bathurst Manor, Wilson Heights, Downsview North            0.000000   
2     Bathurst Manor, Wilson Heights, Downsview North            0.000000   
2     Bathurst Manor, Wilson Heights, Downsview North            0.000000   
2     Bathurst Manor, Wilson Heights, Downsview North            0.000000   
2     Bathurst Manor, Wilson Heights, Downsview North            0.000000   
2     Bathurst Manor, Wilson Heights, Downsview North            0.000000   
2     Bathurst Manor, Wilson Heights, Downsview North            0.000000   
2     Bathurst Manor, Wilson Heights, Downsview North            0.000000   
2     Bathurst Manor, Wilson Heights, Downsview North            0.000000   
2     Bathurst Manor, Wilson Heights, Downsview North            0.000000   
2     Bathurst Manor, Wilson Heights, Downsview North            0.000000   
2     Bathurst Manor, Wilson Heights, Downsview North            0.000000   
2     Bathurst Manor, Wilson Heights, Downsview North            0.000000   
3                                     Bayview Village            0.250000   
3                                     Bayview Village            0.250000   
3                                     Bayview Village            0.250000   
3                                     Bayview Village            0.250000   
4                   Bedford Park, Lawrence Manor East            0.000000   
4                   Bedford Park, Lawrence Manor East            0.000000   
4                   Bedford Park, Lawrence Manor East            0.000000   
4                   Bedford Park, Lawrence Manor East            0.000000   
4                   Bedford Park, Lawrence Manor East            0.000000   
4                   Bedford Park, Lawrence Manor East            0.000000   
4                   Bedford Park, Lawrence Manor East            0.000000   
4                   Bedford Park, Lawrence Manor East            0.000000   
4                   Bedford Park, Lawrence Manor East            0.000000   
4                   Bedford Park, Lawrence Manor East            0.000000   
4                   Bedford Park, Lawrence Manor East            0.000000   
4                   Bedford Park, Law

Cluster 2

In [35]:
trt_merged.loc[trt_merged['Cluster Labels'] == 2]

Neighborhood  Chinese Restaurant  \
39                                   Humberlea, Emery                 0.0   
58  Old Mill South, King's Mill Park, Sunnylea, Hu...                 0.0   

    Cluster Labels  Neighborhood Latitude  Neighborhood Longitude  \
39               2              43.724766              -79.532242   
58               2              43.636258              -79.498509   

              Venue  Venue Latitude  Venue Longitude  Venue Category  
39  Strathburn Park       43.721765       -79.532854  Baseball Field  
58    Woodford Park       43.633152       -79.496266  Baseball Field

Cluster 3

In [36]:
trt_merged.loc[trt_merged['Cluster Labels'] == 3]

Neighborhood  Chinese Restaurant  \
86  West Deane Park, Princess Gardens, Martin Grov...                 0.0   

    Cluster Labels  Neighborhood Latitude  Neighborhood Longitude  \
86               3              43.650943              -79.554724   

                 Venue  Venue Latitude  Venue Longitude Venue Category  
86  Seaforth Golf Club       43.651183       -79.556107    Golf Course

Cluster 4

In [37]:
trt_merged.loc[trt_merged['Cluster Labels'] == 4]

Neighborhood  Chinese Restaurant  \
10                            Caledonia-Fairbanks                 0.0   
10                            Caledonia-Fairbanks                 0.0   
10                            Caledonia-Fairbanks                 0.0   
10                            Caledonia-Fairbanks                 0.0   
26  East Toronto, Broadview North (Old East York)                 0.0   
26  East Toronto, Broadview North (Old East York)                 0.0   
26  East Toronto, Broadview North (Old East York)                 0.0   
26  East Toronto, Broadview North (Old East York)                 0.0   
52                    Moore Park, Summerhill East                 0.0   
61                                      Parkwoods                 0.0   
61                                      Parkwoods                 0.0   
81  The Kingsway, Montgomery Road, Old Mill North                 0.0   
81  The Kingsway, Montgomery Road, Old Mill North                 0.0   
88                                         Weston                 0.0   
88                                         Weston                 0.0   
90                        Willowdale, Newtonbrook                 0.0   
95                                York Mills West                 0.0   
95                                York Mills West                 0.0   

    Cluster Labels  Neighborhood Latitude  Neighborhood Longitude  \
10               4              43.689026              -79.453512   
10               4              43.689026              -79.453512   
10               4              43.689026              -79.453512   
10               4              43.689026              -79.453512   
26               4              43.685347              -79.338106   
26               4              43.685347              -79.338106   
26               4              43.685347              -79.338106   
26               4              43.685347              -79.338106   
52               4              43.689574              -79.383160   
61               4              43.753259              -79.329656   
61               4              43.753259              -79.329656   
81               4              43.653654              -79.506944   
81               4              43.653654              -79.506944   
88               4              43.706876              -79.518188   
88               4              43.706876              -79.518188   
90               4              43.789053              -79.408493   
95               4              43.752758              -79.400049   
95               4              43.752758              -79.400049   

                        Venue  Venue Latitude  Venue Longitude  \
10                SNSD's home       43.690405       -79.455011   
10                 Nairn Park       43.690654       -79.456300   
10              Maximum Woman       43.690651       -79.456333   
10     Fairbank Memorial Park       43.692028       -79.448924   
26               Aldwych Park       43.684901       -79.341091   
26                   The Path       43.683923       -79.335007   
26         Sammon Convenience       43.686951       -79.335007   
26    Donlands Subway Station       43.680960       -79.337759   
52       Loring-Wyle Parkette       43.690270       -79.383438   
61            Brookbanks Park       43.751976       -79.332140   
61              Variety Store       43.751974       -79.333114   
81      Lambton-Kingsway Park       43.657085       -79.508145   
81         Humber River Falls       43.655617       -79.501702   
88                   Elm Park       43.706139       -79.515869   
88  Olympic convenience store       43.704486       -79.515789   
90             Wedgewood park       43.790635       -79.405494   
95          Kitchen Food Fair       43.751298       -79.401393   
95            Tournament Park       43.751257       -79.399717   

       Venue Category  
10               Café  
10               Park  
10      Wo

# Conclusion

After examining five clusters, cluster 1 has the most Chinese restaurants such as Bayview Village, North Toronto Wes, etc. The cluster results suggests that the client can open a Chinese restaurant in potential neighborhoods with less Chinese restaurant. Cluster 4 has several good potential neighborhoods because they are close to cluster but have no Chinese restaurant. This way, client can gain profit while minimize competition. 